Lambda School Data Science

*Unit 4, Sprint 1, Module 3*

---

# Document Classification (Prepare)

Today's guided module project will be different. You already know how to do classification. You ready know how to extract features from documents. So? That means you're ready to combine and practice those skills in a kaggle competition. We we will open with a five minute sprint explaining the competition, and then give you 25 minutes to work. After those twenty five minutes are up, I will give a 5-minute demo an NLP technique that will help you with document classification (*and **maybe** the competition*).

Today's all about having fun and practicing your skills. The competition will begin

## Learning Objectives
* <a href="#p1">Part 1</a>: Text Feature Extraction & Classification Pipelines
* <a href="#p2">Part 2</a>: Latent Semantic Indexing
* <a href="#p3">Part 3</a>: Word Embeddings with Spacy

# Text Feature Extraction & Classification Pipelines (Learn)
<a id="p1"></a>

## Overview

Sklearn pipelines allow you to stitch together multiple components of a machine learning process. The idea is that you can pass you raw data and get predictions out of the pipeline. This ability to pass raw input and receive a prediction from a singular class makes pipelines well suited for production, because you can pickle a a pipeline without worry about other data preprocessing steps. 

*Note:* Each time we call the pipeline during grid search, each component is fit again. The vectorizer (tf-idf) is transforming our entire vocabulary during each cross-validation fold. That transformation adds significant run time to our grid search. There *might* be interactions between the vectorizer and our classifier, so we estimate their performance together in the code below. However, if your goal is to reduce run time. Train your vectorizer separately (ie out of the grid-searched pipeline). 

In [1]:
# Import Statements
from sklearn.pipeline import Pipeline
from sklearn.datasets import fetch_20newsgroups
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer

In [22]:
# Dataset
from sklearn.datasets import fetch_20newsgroups

categories = ['talk.politics.misc',
              'sci.space']

data = fetch_20newsgroups(subset='train', categories=categories, remove=('headers', 'footers', 'quotes'))

In [23]:
data['data'][2]

"\nMy opinion is this:  In a society whose economy is primarily based on \ncapitalism, the role of government should be to provide those goods and \nservices that need providing for the general public's good.  BUT government \nshould supply those necessary goods and services only when it is impossible \nfor a private enterprise (or individual) to make money from providing them.\nI agree with some of the other posts that this train probably can not make \nmoney and will rely heavily on State tax dollars.  \n\nThe question, I think, then becomes:  Do we, the general public, need the train?\n\nI certainly do not, nor will I ever, need this train in Lubbock, Texas.  With\nthe inexpensive air travel provided between Dallas and Houston, I don't think\npeople in Dallas or Houston need it either."

In [24]:
#print out data sample
data.keys()

dict_keys(['data', 'filenames', 'target_names', 'target', 'DESCR'])

In [25]:
# Create Pipeline Components
# instantiate our TfidVectorizer and model
vect = TfidfVectorizer(stop_words='english', ngram_range=(1,2))
rfc = RandomForestClassifier()

In [26]:
data['data']

['\nIn billions of dollars (%GNP):\nyear  GNP    receipts     outlays       deficit     debt    unempl%  admin\n====  ====   ===========  ============  =========   ======  =======  =======\n1977  1930   355.6 (18.4) 409.2  (21.2) 53.6 (2.8)   709.1           Carter\n1978  2174   399.6 (18.4) 458.7  (21.1) 59.2 (2.7)   780.4           Carter\n1979  2444   463.3 (19.0) 503.5  (20.6) 40.2 (1.6)   833.8           Carter\n1980  2674   517.1 (19.3) 590.9  (22.1) 73.8 (2.8)   914.3   7.9     Carter\n1981  2986   599.3 (20.1) 678.2  (22.7) 78.9 (2.6)  1003.9   8.4     Reagan\n1982  3130   617.8 (19.7) 745.7  (23.8) 127.9 (4.1) 1147.0  11.0     Reagan\n1983  3325   600.6 (18.1) 808.3  (24.3) 207.8 (6.2) 1381.9  10.9     Reagan\n1984  3688   666.5 (18.1) 851.8  (23.1) 185.3 (5.0) 1576.7   8.6     Reagan\n1985  3958   734.1 (18.5) 946.3  (23.9) 212.3 (5.4) 1827.5   8.1     Reagan\n1986  4177   769.1 (18.4) 989.8  (23.7) 220.7 (5.3) 2129.5   7.9     Reagan\n1987  4442   854.1 (19.2) 1002.1 (22.6) 

In [27]:
len(data['data'])

1058

In [28]:
data['target']

array([1, 1, 1, ..., 1, 0, 0])

In [29]:
data['target'].shape

(1058,)

In [30]:
# Define the Pipeline
# We used make_pipeline in Unit 2 Pipline is more verbose and we can name vector as vect
# make_pipeline you can't name things explicitly
pipe = Pipeline([
                 #Vectorizer
                 ('vect', vect),
                 # Classifier
                 ('clf', rfc)
                ])

# The pipeline puts together a bunch fit then transform,fit then predict. 

In [31]:
parameters = {
    'vect__max_df': ( 0.75, 1.0),
    'vect__min_df': (.02, .05),
    'vect__max_features': (500,1000),
    'clf__n_estimators':(5, 10,),
    'clf__max_depth':(15,20)
}

grid_search = GridSearchCV(pipe,parameters, cv=5, n_jobs=-1, verbose=1)
grid_search.fit(data.data, data.target)

Fitting 5 folds for each of 32 candidates, totalling 160 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    5.7s
[Parallel(n_jobs=-1)]: Done 160 out of 160 | elapsed:   20.5s finished


GridSearchCV(cv=5, error_score=nan,
             estimator=Pipeline(memory=None,
                                steps=[('vect',
                                        TfidfVectorizer(analyzer='word',
                                                        binary=False,
                                                        decode_error='strict',
                                                        dtype=<class 'numpy.float64'>,
                                                        encoding='utf-8',
                                                        input='content',
                                                        lowercase=True,
                                                        max_df=1.0,
                                                        max_features=None,
                                                        min_df=1,
                                                        ngram_range=(1, 2),
                                                        no

In [32]:
grid_search.best_score_

0.8345658588929625

In [33]:
grid_search.best_params_

{'clf__max_depth': 20,
 'clf__n_estimators': 10,
 'vect__max_df': 1.0,
 'vect__max_features': 1000,
 'vect__min_df': 0.02}

In [36]:
grid_search.predict(['This is a free society', 
                     'Elections will be in November', 
                     "Covid doesn't care what your political beliefs are.",
                    'The team successfully launced their satellite into low-earth orbit', 
                     'The information paradox was solved last week, say some scientist.', 
                     'We will be living on Mars in 2050.'])

array([1, 0, 1, 0, 1, 0])

In [48]:
data['target_names']

['sci.space', 'talk.politics.misc']

In [37]:
grid_search.predict_proba(['This is a free society', 
                     'Elections will be in November', 
                     "Covid doesn't care what your political beliefs are.",
                    'The team successfully launced their satellite into low-earth orbit', 
                     'The information paradox was solved last week, say some scientist.', 
                     'We will be living on Mars in 2050.'])

array([[0.48242864, 0.51757136],
       [0.6113385 , 0.3886615 ],
       [0.45168731, 0.54831269],
       [0.89283112, 0.10716888],
       [0.4827682 , 0.5172318 ],
       [0.54935933, 0.45064067]])

In [38]:
from sklearn.model_selection import RandomizedSearchCV

In [43]:
import scipy

parameters = {
    'vect__max_df': scipy.stats.uniform(0.8, 0.99),
    'vect__min_df': scipy.stats.uniform(0.01, 0.05),
    'vect__max_features': scipy.stats.randint(500,1000),
    'clf__n_estimators': scipy.stats.randint(30, 100),
    'clf__max_depth': scipy.stats.randint(20, 100)
}
# importing the scipy library
rand_search = RandomizedSearchCV(pipe, parameters, cv=3, n_jobs=-1, verbose=-1, n_iter=25)
rand_search.fit(data['data'], data['target'])

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  56 tasks      | elapsed:   10.2s
[Parallel(n_jobs=-1)]: Done  75 out of  75 | elapsed:   13.3s finished


RandomizedSearchCV(cv=3, error_score=nan,
                   estimator=Pipeline(memory=None,
                                      steps=[('vect',
                                              TfidfVectorizer(analyzer='word',
                                                              binary=False,
                                                              decode_error='strict',
                                                              dtype=<class 'numpy.float64'>,
                                                              encoding='utf-8',
                                                              input='content',
                                                              lowercase=True,
                                                              max_df=1.0,
                                                              max_features=None,
                                                              min_df=1,
                                                        

In [44]:
rand_search.best_score_

0.8601006524165165

In [45]:
rand_search.best_params_

{'clf__max_depth': 89,
 'clf__n_estimators': 73,
 'vect__max_df': 1.7438692581092055,
 'vect__max_features': 854,
 'vect__min_df': 0.013583741448340566}

In [47]:
data['target_names']

['sci.space', 'talk.politics.misc']

In [46]:
rand_search.predict(['This is a free society', 
                     'Elections will be in November', 
                     "Covid doesn't care what your political beliefs are.",
                    'The team successfully launced their satellite into low-earth orbit', 
                     'The information paradox was solved last week, say some scientist.', 
                     'We will be living on Mars in 2050.'])

array([1, 0, 0, 0, 0, 0])

In [41]:
scipy.stats.uniform(0.8, 0.99)

In [42]:
import numpy as np

np.random.uniform(0.8, 0.99)

0.9513932341059467

## Follow Along 

What you should be doing now:
1. Join the Kaggle Competition
2. Download the data
3. Train a model (try using the pipe method I just demoed)

## Challenge

You're trying to achieve 75% Accuracy on your model.

## Latent Semantic Indexing (Learn)
<a id="p2"></a>

## Overview

In [49]:
# Singular Value Decomposition

# Import

from sklearn.decomposition import TruncatedSVD

svd = TruncatedSVD(n_components=100, # Just here for demo. 
                   algorithm='randomized',
                   n_iter=10)

In [50]:
params = { 
    'lsi__svd__n_components': [10,100,250],
    'lsi__vect__max_df':[.9, .95, 1.0],
    'clf__n_estimators':[5,10,20]
}

In [51]:
# LSI
lsi = Pipeline([('vect', vect), ('svd', svd)])


# Pipe
pipe = Pipeline([('lsi', lsi), ('clf', rfc)])

In [84]:
params = {
    'lis__svd__n_components': scipy.stats.randint(10, 100),
    'lis__vect__max_df': scipy.stats.uniform(0.8, 0.99),
    'clf__n_estimators': scipy.stats.randint(10, 100)
}

In [85]:
print(pipe)

Pipeline(memory=None,
         steps=[('lsi',
                 Pipeline(memory=None,
                          steps=[('vect',
                                  TfidfVectorizer(analyzer='word', binary=False,
                                                  decode_error='strict',
                                                  dtype=<class 'numpy.float64'>,
                                                  encoding='utf-8',
                                                  input='content',
                                                  lowercase=True, max_df=1.0,
                                                  max_features=None, min_df=1,
                                                  ngram_range=(1, 2), norm='l2',
                                                  preprocessor=None,
                                                  smooth_idf=True,
                                                  stop_words='english',
                                                  strip_a

In [ ]:
# Fit
grid_search = GridSearchCV(pipe,params, cv=5, n_jobs=-1, verbose=1)
grid_search.fit(data.data, data.target)

In [ ]:
grid_search.best_score_

In [55]:
rand_search = RandomizedSearchCV(pipe, params, n_iter=20, cv=3, n_jobs=-1, verbose=1)
rand_search.fit(data.data, data.target)

Fitting 3 folds for each of 20 candidates, totalling 60 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:  2.0min
[Parallel(n_jobs=-1)]: Done  60 out of  60 | elapsed:  3.2min finished


RandomizedSearchCV(cv=3, error_score=nan,
                   estimator=Pipeline(memory=None,
                                      steps=[('lsi',
                                              Pipeline(memory=None,
                                                       steps=[('vect',
                                                               TfidfVectorizer(analyzer='word',
                                                                               binary=False,
                                                                               decode_error='strict',
                                                                               dtype=<class 'numpy.float64'>,
                                                                               encoding='utf-8',
                                                                               input='content',
                                                                               lowercase=True,
                          

In [64]:
best_pipeline = rand_search.best_estimator_

In [65]:
# very high dimensionality
best_pipeline.named_steps['lsi'].named_steps['vect'].transform([data['data'][0]]).todense().shape

(1, 123386)

In [67]:
rand_search.best_params_

{'lsi__vect__max_df': 0.9,
 'lsi__svd__n_components': 100,
 'clf__n_estimators': 20}

In [66]:
best_pipeline.named_steps['lsi'].transform([data['data'][1]]).shape

(1, 100)

## Follow Along
1. Join the Kaggle Competition
2. Download the data
3. Train a model & try: 
    - Creating a Text Extraction & Classification Pipeline
    - Tune the pipeline with a `GridSearchCV` or `RandomizedSearchCV`
    - Add some Latent Semantic Indexing (lsi) into your pipeline. *Note:* You can grid search a nested pipeline, but you have to use double underscores ie `lsi__svd__n_components`
4. Make a submission to Kaggle 


## Challenge

Continue to apply Latent Semantic Indexing (LSI) to various datasets. 

# Word Embeddings with Spacy (Learn)
<a id="p3"></a>

# Overview

In [68]:
import spacy
nlp = spacy.load("en_core_web_lg")

In [69]:
doc = nlp("Two bananas in pyjamas")

In [70]:
bananas_vector = doc.vector
print(len(bananas_vector))

300


In [71]:
def get_word_vectors(docs):
    return [nlp(doc).vector for doc in docs]

In [75]:
%%time
X = get_word_vectors(data.data)

len(X) == len(data.data)

CPU times: user 50.2 s, sys: 3.66 s, total: 53.9 s
Wall time: 54.1 s


True

In [77]:
X[0].shape

(300,)

In [76]:
X

[array([-6.39469251e-02,  1.15542449e-01, -2.61393748e-02, -5.09804077e-02,
         7.21615106e-02, -1.44754173e-02, -2.45486461e-02, -1.69383350e-03,
         5.13066202e-02,  2.77939290e-01, -1.76008210e-01,  1.94453418e-01,
         3.84156704e-02, -5.77316061e-02,  5.28421719e-03,  5.29024564e-02,
        -1.15618937e-01,  8.21520627e-01, -1.88263014e-01,  2.10277047e-02,
        -6.70138896e-02, -1.25301164e-02, -1.01395071e-01, -3.48230340e-02,
         5.50318249e-02, -1.36584938e-01,  2.52550305e-03, -3.73862311e-02,
         4.68657427e-02,  9.89785269e-02, -6.69576824e-02,  9.91502590e-03,
        -5.57734855e-02, -1.82886403e-02,  3.43844518e-02, -6.72312006e-02,
        -4.91568167e-03,  8.72865990e-02, -3.15189138e-02,  1.39028221e-01,
         1.64764430e-02, -1.74005292e-02,  2.07627907e-01,  1.83482319e-02,
        -5.03463149e-02, -1.17296927e-01,  1.31884133e-02,  1.72613367e-01,
        -1.20632094e-03, -2.26643514e-02,  7.18180975e-03,  3.15846428e-02,
         1.2

In [78]:
len(X)

1058

In [79]:
rfc.fit(X, data['target'])

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [80]:
rfc.score(X, data['target'])

0.9877126654064272

In [81]:
from multiprocessing import Pool, cpu_count

In [82]:
cpu_count()

8

In [83]:
pool = Pool(3)

## Follow Along

## Challenge

What you should be doing now:
1. Join the Kaggle Competition
2. Download the data
3. Train a model & try: 
    - Creating a Text Extraction & Classification Pipeline
    - Tune the pipeline with a `GridSearchCV` or `RandomizedSearchCV`
    - Add some Latent Semantic Indexing (lsi) into your pipeline. *Note:* You can grid search a nested pipeline, but you have to use double underscores ie `lsi__svd__n_components`
    - Try to extract word embeddings with Spacy and use those embeddings as your features for a classification model.
4. Make a submission to Kaggle 

# Review

To review this module: 
* Continue working on the Kaggle competition
* Find another text classification task to work on